<center><H1>Modelado con LSTMs bidireccionales para la predicción de la demanda de energía eléctrica en la ZC Hermosillo</H1><center>

<center><img src="https://www.gstatic.com/devrel-devsite/prod/ve2848ad92313fddfcd40baeb58a2f663fe2fd55c371a714a6bb3e329e2b15223/tensorflow/images/lockup.svg"  height="80px" style="padding-bottom:5px;"  /></center>

<center><H2>Julio Waissman Vilanova</H2>

<table align="center">
      <td align="center"><a target="_blank" href="https://www.unison.mx">
            <img src="https://www.unison.mx/wp-content/themes/awaken/images/logo.png"  height="70px" style="padding-bottom:5px;"  /></a></td>  
      <td align="center"><a target="_blank" href="https://www.gob.mx/cenace">
            <img src="https://universidad.cenace.gob.mx/pluginfile.php/244/block_html/content/CENACE-logo-completo.png" width="300" style="padding-bottom:5px;" /></a></td>
      <td align="center"><a target="_blank" href="https://colab.research.google.com/github/juliowaissman/rn-cenace/blob/main/biLSTM_Hmo.ipynb">
            <img src="https://i.ibb.co/2P3SLwK/colab.png"  style="padding-bottom:5px;" />Ejecuta en Google Colab</a></td>

</table>

En esta libreta vamos a replicar el modelo utilizado en el artículo *Weather Based Day-Ahead and Week-Ahead Load Forecasting using Deep Recurrent Neural Network* de Mingzhe Zou, Duo Fang, Gareth Harrison y Sasa Djokic (IEEExplore, DOI: 978-1-7281-3815-2/19). El texto lo puedes consultar [aquí](https://www.researchgate.net/publication/337220913_Weather_Based_Day-Ahead_and_Week-Ahead_Load_Forecasting_using_Deep_Recurrent_Neural_Network)


In [3]:
# Las bibliotecas de base
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

# Para normalizar los datos de entrada
from sklearn.preprocessing import MinMaxScaler

#Tensorflow con keras
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

# Gráficas más fáciles de manipular con plotly
import plotly.express as px
import plotly.graph_objects as go

# Como se verán las gráficas de matplotlib
plt.style.use('ggplot')
plt.rcParams['figure.figsize'] = (15,7)

## 1. Introducción

En esta libreta les toca ahora hacer una red neuronal tal como lo hicimos para la GRNO pero para 3 zonas de carga diferentes (Hermosillo, Nogales y Guaymas). Aquí tenemos la ventaja que se pueden agregar varias variables muy interesantes.

## 2. Descargar los datos

Empecemos por cargar los datos:

In [4]:
#url_gym = "https://github.com/juliowaissman/rn-cenace/raw/main/proyectos/Hector/dataset_gym.xlsx"
url_hmo = "https://github.com/juliowaissman/rn-cenace/raw/main/proyectos/Hector/dataset_hmo.xlsx"
#url_nog = "https://github.com/juliowaissman/rn-cenace/raw/main/proyectos/Hector/dataset_nog.xlsx"

df_raw = pd.read_excel(url_hmo)
df_raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50415 entries, 0 to 50414
Data columns (total 7 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   Date             50415 non-null  datetime64[ns]
 1   Demand           50415 non-null  float64       
 2   Temperature      50415 non-null  float64       
 3   PrecipIntensity  50415 non-null  float64       
 4   Humidity         50415 non-null  float64       
 5   WindSpeed        50415 non-null  float64       
 6   Zona             50415 non-null  object        
dtypes: datetime64[ns](1), float64(5), object(1)
memory usage: 2.7+ MB


In [5]:
df = df_raw.copy()
df.set_index(df.Date, inplace=True)

# Aqui es donde faltan datos
print(df.Date[df.Date.diff() > pd.to_timedelta(1,'h')])

# Aqui los reponemos copiando el dato anterior
df = df.asfreq('H', method='pad')
df['Mes'] = df.index.month
df['Semana'] = df.index.weekofyear
df['Dia'] = df.index.weekday
df['Hora'] = df.index.hour

Date
2021-10-01 18:00:00   2021-10-01 18:00:00
Name: Date, dtype: datetime64[ns]


/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:10: FutureWarning:

weekofyear and week have been deprecated, please use DatetimeIndex.isocalendar().week instead, which returns a Series.  To exactly reproduce the behavior of week and weekofyear and return an Index, you may call pd.Int64Index(idx.isocalendar().week)



In [6]:
fig = px.line(df, x="Date", y="Demand", title='Demanda de energía ZC Hermosillo')
fig.show()

fig = px.line(df, x="Date", y="Temperature", title='Temperatura ZC Hermosillo')
fig.show()

fig = px.scatter_matrix(df, dimensions=["Demand", "Temperature", "PrecipIntensity", "Humidity", "WindSpeed"])
fig.show()


## 3. Acondicionamiento de datos para el aprendizaje

Seleccionamos datos de entrenamiento y prueba, asumiendo que Tensorflow escoje de forma automática la mejor partición entre datos de entrenamiento y de validación.

In [7]:
df_train = df[df.index.year < 2021]
df_test = df[df.index.year == 2021]

df_train.shape, df_test.shape

((43824, 11), (6593, 11))

Debido al algoritmo de B-prop a través del tiempo, las RNN son muy sensibles a los valores de los datos de entrada (en particular las LSTMs) por lo que es importante normalizar los datos. Notese que vamos a ajustar el `scaler` con los datos de entrenamiento, y se usa el mismo para ajustar los datos de prueba.

Vamos a generar los objetos `scaler` necesarios para escalar a todas las variables que estamos utilizando.

In [8]:
# Vamos a ver cuales son los atributos que tenemos
df_train.columns

Index(['Date', 'Demand', 'Temperature', 'PrecipIntensity', 'Humidity',
       'WindSpeed', 'Zona', 'Mes', 'Semana', 'Dia', 'Hora'],
      dtype='object')

In [9]:
selected_attr = ['Demand', 'Temperature', 'PrecipIntensity', 
                 'Humidity', 'WindSpeed', 'Semana', 'Dia', 'Hora'] 

train = df_train[selected_attr].copy()
scalers = {}  # Un diccionario con los scalers

for attr in selected_attr:
  scaler = MinMaxScaler(feature_range=(-1, 1))
  s_s = scaler.fit_transform(train[attr].values.reshape(-1,1))
  scalers[attr] = scaler
  train[attr] = s_s.ravel()

train.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 43824 entries, 2016-01-02 00:00:00 to 2020-12-31 23:00:00
Freq: H
Data columns (total 8 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   Demand           43824 non-null  float64
 1   Temperature      43824 non-null  float64
 2   PrecipIntensity  43824 non-null  float64
 3   Humidity         43824 non-null  float64
 4   WindSpeed        43824 non-null  float64
 5   Semana           43824 non-null  float64
 6   Dia              43824 non-null  float64
 7   Hora             43824 non-null  float64
dtypes: float64(8)
memory usage: 3.0 MB


y ahora vamos a escalar los datos de `val` y `test` con el `scaler` ajustado:

In [10]:
test = df_test[selected_attr].copy()
for attr in selected_attr:
  scaler = scalers[attr]
  s_s = scaler.transform(test[attr].values.reshape(-1,1))
  test[attr] = s_s.ravel()

test.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 6593 entries, 2021-01-01 00:00:00 to 2021-10-02 16:00:00
Freq: H
Data columns (total 8 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   Demand           6593 non-null   float64
 1   Temperature      6593 non-null   float64
 2   PrecipIntensity  6593 non-null   float64
 3   Humidity         6593 non-null   float64
 4   WindSpeed        6593 non-null   float64
 5   Semana           6593 non-null   float64
 6   Dia              6593 non-null   float64
 7   Hora             6593 non-null   float64
dtypes: float64(8)
memory usage: 463.6 KB


Pero esto no es suficiente para poder entrenar una red neuronal. Para poder entrenar la red necesitamos convertir los datos en muestras de entradas con observaciones pasada y con salidas futuras. para ser usados en el entrenamiento.

Vamos a hacer una función para esto:

In [11]:
def divide_series(series, n_pasado, n_futuro, n_salto, es_train=True):
  """
  n_pasado: número de observaciones pasadas para el encoder 
  n_futuro: número de observaciones futuras
  n_salto: a partir de donde empiezan a contar las observaciones futuras

  """
  X, y = list(), list() # Vamos a crear listas y al final hacemos ndarrays
  generador = range(series.shape[0]) if es_train else range(0, series.shape[0], n_futuro)
  
  for ini in generador:
    fin_anterior = ini + n_pasado
    fin_actual = fin_anterior + n_salto + n_futuro
    if fin_actual > len(series):
      break
    pasado = series[ini: fin_anterior, :]
    futuro = series[fin_anterior + n_salto: fin_actual, 0].reshape(-1, 1)
    X.append(pasado)
    y.append(futuro)
  return np.array(X), np.array(y)

De acuerdo al artículo vamos a usar los últimos 28 días tanto para la predicción a 1 día como la predicción a 7 días (vamos a empezar con la predicción a 1 día

In [38]:
n_pasado = 24 * 7 + 12
n_futuro = 24
n_salto = 12

y ahora vamos a generar nuestos conjuntos de aprendizaje:

In [39]:
# Atributos a utilizar

n_attr = len(selected_attr)

X_train, y_train = divide_series(train.values, n_pasado, n_futuro, n_salto)
X_test, y_test = divide_series(test.values, n_pasado, n_futuro, n_salto, es_train=False)


# Reacomodar como un tensor de 3 dimensiones
X_train = X_train.reshape((X_train.shape[0], X_train.shape[1], n_attr))
X_test = X_test.reshape((X_test.shape[0], X_test.shape[1], n_attr))

y_train = y_train.reshape((y_train.shape[0], y_train.shape[1], 1))
y_test = y_test.reshape((y_test.shape[0], y_test.shape[1], 1))

X_train.shape, X_test.shape, y_train.shape, y_test.shape


((43609, 180, 8), (266, 180, 8), (43609, 24, 1), (266, 24, 1))

## 4. Modelo neuronal

Aqui vamos a poner el modelo neuronal con la estructura que se recomienda en el artículo. Existen diferencias de lo que estamos haciendo respecto a lo que hace el artículo:

1. No estamos usando valores predictivos en las variables de calendario o meteorológicas, esperamos un error mayor debido a esto.

2. No queda claro como insertan y hacen la predicción en el artículo, si con todos los valores cada media hora o sólo los valores por cada día.

3. No se agregó la variable de días festivos o las de posición solar, es necesario agregarlas.

In [53]:
# El modelo

inputs = layers.Input(shape=(n_pasado, n_attr))
#-------------------------------------------------------
bi_1 = layers.Bidirectional(
  layers.LSTM(100, return_sequences=True,
              kernel_regularizer=keras.regularizers.l2(0.0005))
)
d_1 = layers.Dropout(0.5)
outputs_l1 = d_1(bi_1(inputs))
#-------------------------------------------------------
bi_2 = layers.Bidirectional(
  layers.LSTM(100, #return_sequences=True,
              kernel_regularizer=keras.regularizers.l2(0.0005))
)
d_2 = layers.Dropout(0.5)
outputs_l2 = d_2(bi_2(outputs_l1))
#-------------------------------------------------------
bi_3 = layers.Bidirectional(
  layers.LSTM(100, kernel_regularizer=keras.regularizers.l2(0.0005))
)
d_3 = layers.Dropout(0.5)
#outputs_l3 = d_3(bi_3(outputs_l2))
#-------------------------------------------------------
densa = layers.Dense(n_futuro)
outputs = densa(outputs_l2)


modelo = keras.models.Model(inputs, outputs)

# Y con esto terminamos con el modelo
modelo.summary()

Model: "model_16"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_20 (InputLayer)        [(None, 180, 8)]          0         
_________________________________________________________________
bidirectional_50 (Bidirectio (None, 180, 200)          87200     
_________________________________________________________________
dropout_50 (Dropout)         (None, 180, 200)          0         
_________________________________________________________________
bidirectional_51 (Bidirectio (None, 200)               240800    
_________________________________________________________________
dropout_51 (Dropout)         (None, 200)               0         
_________________________________________________________________
dense_16 (Dense)             (None, 24)                4824      
Total params: 332,824
Trainable params: 332,824
Non-trainable params: 0
____________________________________________________

## 5 Entrenando el modelo

Vamos ahora a aprovechar para ver como se usa un método de calendarización de la tasa de aprendizaje. Revisa que tengas un modelo válido.


In [54]:
path_checkpoint = "model_checkpoint.h5"
modelckpt_callback = keras.callbacks.ModelCheckpoint(
    monitor="val_loss",
    filepath=path_checkpoint,
    verbose=1,
    save_weights_only=True,
    save_best_only=True,
)


es_callback = keras.callbacks.EarlyStopping(
    monitor="val_loss", 
    min_delta=0, 
    patience=5
)

modelo.compile(
    optimizer="adam", 
    loss="mae"
)

history = modelo.fit(
    X_train,
    y_train,
    epochs=25,
    validation_split=0.2,
    batch_size=32,
    callbacks=[es_callback, modelckpt_callback]
)

Epoch 1/25
1091/1091 [==============================] - 660s 599ms/step - loss: 0.1322 - val_loss: 0.0803

Epoch 00001: val_loss improved from inf to 0.08029, saving model to model_checkpoint.h5
Epoch 2/25
1091/1091 [==============================] - 650s 596ms/step - loss: 0.0865 - val_loss: 0.0683

Epoch 00002: val_loss improved from 0.08029 to 0.06825, saving model to model_checkpoint.h5
Epoch 3/25
1091/1091 [==============================] - 652s 598ms/step - loss: 0.0815 - val_loss: 0.0696

Epoch 00003: val_loss did not improve from 0.06825
Epoch 4/25
1091/1091 [==============================] - 650s 596ms/step - loss: 0.0789 - val_loss: 0.0688

Epoch 00004: val_loss did not improve from 0.06825
Epoch 5/25
1091/1091 [==============================] - 652s 597ms/step - loss: 0.0777 - val_loss: 0.0796

Epoch 00005: val_loss did not improve from 0.06825
Epoch 6/25
1091/1091 [==============================] - 652s 597ms/step - loss: 0.0756 - val_loss: 0.0763

Epoch 00006: val_loss did

Guarda el modelo final antes que paso otra cosa

Apliquemos el modelo a X_test

In [55]:
y_est = modelo.predict(X_test)
y_test.ravel().shape, y_est.ravel().shape, test.index[n_pasado + n_salto:-17].shape

((6384,), (6384,), (6384,))

¿Ya revisante los parámetros? 

In [56]:
scaler = scalers['Demand']

yr = scaler.inverse_transform(y_test.ravel().reshape(-1, 1))
yh = scaler.inverse_transform(y_est.ravel().reshape(-1, 1))

df_est = pd.DataFrame({
    "Real": yr.ravel(),
    "Estimado": yh.ravel(),
    "Fecha": test.index[n_pasado + n_salto:-17]     
})

Y por último vamos a graficar la salida estimada con plotly

In [57]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_est.Fecha, y=df_est.Estimado, name="Estimada"))
fig.add_trace(go.Scatter(x=df_est.Fecha, y=df_est.Real, name="Real"))
fig.update_layout(title="Estimación de la demanda")
fig.show()

In [51]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [58]:
modelo.save("drive/MyDrive/Cenace-tf-models/hmo-bidir-2-capa.h5", save_format='h5')